In [ ]:
from google.colab import files
uploads=files.upload()

Saving all-data.csv to all-data (1).csv


In [ ]:
import pandas as pd
import csv
data_df=pd.read_csv('/content/all-data.csv',encoding="ISO-8859-1",names=['sentiment','text'])
print(data_df)

     sentiment                                               text
0      neutral  According to Gran , the company has no plans t...
1      neutral  Technopolis plans to develop in stages an area...
2     negative  The international electronic industry company ...
3     positive  With the new production plant the company woul...
4     positive  According to the company 's updated strategy f...
...        ...                                                ...
4841  negative  LONDON MarketWatch -- Share prices ended lower...
4842   neutral  Rinkuskiai 's beer sales fell by 6.5 per cent ...
4843  negative  Operating profit fell to EUR 35.4 mn from EUR ...
4844  negative  Net sales of the Paper segment decreased to EU...
4845  negative  Sales in Finland decreased by 10.5 % in Januar...

[4846 rows x 2 columns]


In [ ]:
def build_vocab(data_df):
  uniq_cat=data_df['sentiment'].unique()
  sep_doc_dict=dict()
  sep_term_dict=dict()
  for cat in uniq_cat:
    sep_doc_dict[cat]=list()
  for cat in uniq_cat:
    df_temp=data_df[data_df['sentiment']==cat]
    sep_doc_dict[cat].extend(df_temp['text'].values)
    sep_term_dict[cat]=[txt.split() for txt in sep_doc_dict[cat]]
  doc_wd_list=[txt.split() for txt in data_df['text'].values]
  full_txt=' '.join(data_df['text'].values)
  word_list=set(full_txt.split())
  return word_list,sep_term_dict,sep_doc_dict
print(build_vocab(data_df))

({'600mn', 'MW', 'Palm', 'ERCs', 'centralising', 'Consisting', 'Gallup', 'Total', 'ADPnews', 'meteorological', '710.3', '087', 'glasses', 'pre-tax', 'Wilson', 'euro0', 'magazine', '3.3', 'Eesti', 'Oyj', 'pressurized', 'Solution', 'Wipro', 'mostly', 'opinion', 'Ericsson', 'Slovenia', 'publisher', 'centres', 'latter', '164.7', 'bus', 'rebuilt', 'functions', 'finances', '253', 'headcount', 'Brand', 'Commerzbank', 'EUR11', 'story', 'Founded', 'bodily', '180mn', 'sell-off', 'Cash', 'Agriculture', '0.37', 'now', 'just', 'Chemicals', 'expires', 'Kasola', 'Wisconsin', 'emphasises', 'TPS1V)said', 'Increase', 'weighted', 'geo-location', 'perch', '40.5', 'A-B-C', 'Valmet', 'manufacture', 'March-April', 'SEK150', 'events', '.03', 'stands', 'rotation', 'confidence', 'Seitovirta', 'corroborate', 'Deutsche', 'Shane', 'hydrocarbon', 'moulding', 'hired', 'remaining', 'opportunity', 'Kitron', 'confirmations', '6.3', '3.5', 'EUR25', 'transaction', 'domain', 'rationalize', '25.3', 'Protein', '380', 'Kauko

In [ ]:
from os import setgroups
import math
def term_frequency_icf_find(data_df):
  vocab,sep_term_dict,sep_doc_dict=build_vocab(data_df)
  term_freq_dict=dict()
  icf_dict=dict()
  for wd in vocab:
    term_freq_dict[wd]=dict()
    for cat in sep_term_dict.keys():
      term_freq_dict[wd][cat]=0
  for cat in sep_term_dict.keys():
    for wd_list in sep_term_dict[cat]:
      for wd in wd_list:
        term_freq_dict[wd][cat]=term_freq_dict[wd][cat]+1
  for wd in vocab:
    cnt=0
    for cat in term_freq_dict[wd]:
      if term_freq_dict[wd][cat]>0:
        cnt+=1
    icf_dict[wd]=math.log(float(3/cnt))
  return term_freq_dict,icf_dict

In [ ]:
print(term_frequency_icf_find(data_df))

({'600mn': {'neutral': 1, 'negative': 0, 'positive': 0}, 'MW': {'neutral': 9, 'negative': 0, 'positive': 1}, 'Palm': {'neutral': 1, 'negative': 0, 'positive': 1}, 'ERCs': {'neutral': 1, 'negative': 0, 'positive': 0}, 'centralising': {'neutral': 0, 'negative': 0, 'positive': 1}, 'Consisting': {'neutral': 1, 'negative': 0, 'positive': 0}, 'Gallup': {'neutral': 1, 'negative': 0, 'positive': 0}, 'Total': {'neutral': 2, 'negative': 0, 'positive': 1}, 'ADPnews': {'neutral': 2, 'negative': 8, 'positive': 2}, 'meteorological': {'neutral': 0, 'negative': 0, 'positive': 1}, '710.3': {'neutral': 1, 'negative': 0, 'positive': 0}, '087': {'neutral': 1, 'negative': 0, 'positive': 0}, 'glasses': {'neutral': 1, 'negative': 0, 'positive': 0}, 'pre-tax': {'neutral': 1, 'negative': 2, 'positive': 4}, 'Wilson': {'neutral': 2, 'negative': 0, 'positive': 1}, 'euro0': {'neutral': 0, 'negative': 0, 'positive': 1}, 'magazine': {'neutral': 12, 'negative': 3, 'positive': 3}, '3.3': {'neutral': 2, 'negative': 1, 

In [ ]:
def make_category_prob(data_df):
  cat_prob_dict=dict()
  cat_uniq=data_df['sentiment'].unique()
  l=len(data_df)
  for cat in cat_uniq:
    data_part=data_df[data_df['sentiment']==cat]
    lp=len(data_part)
    cat_p=lp/l
    cat_prob_dict[cat]=cat_p
  return cat_prob_dict


In [ ]:
print(make_category_prob(data_df))

{'neutral': 0.594098225340487, 'negative': 0.12463887742468015, 'positive': 0.28126289723483283}


In [ ]:
def get_tf_icf_score(data_df):
  tf_icf_dict=dict()
  tf_icf_prob=dict()
  tf_dict,icf_dict=term_frequency_icf_find(data_df)
  for wd in tf_dict.keys():
    tf_icf_dict[wd]=dict()
    for cat in tf_dict[wd].keys():
       tf_icf_dict[wd][cat]=tf_dict[wd][cat]*icf_dict[wd]
  for wd in tf_dict.keys():
    tf_icf_prob[wd]=dict()
    for cat in tf_dict[wd].keys():
       s=sum(tf_icf_dict[wd].values())
       if s>0:
          tf_icf_prob[wd][cat]=tf_icf_dict[wd][cat]/s
       else:
         tf_icf_prob[wd][cat]=0
      
  return tf_icf_dict,tf_icf_prob

In [ ]:
print(get_tf_icf_score(data_df))

({'600mn': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, 'MW': {'neutral': 3.6491859729734797, 'negative': 0.0, 'positive': 0.4054651081081644}, 'Palm': {'neutral': 0.4054651081081644, 'negative': 0.0, 'positive': 0.4054651081081644}, 'ERCs': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, 'centralising': {'neutral': 0.0, 'negative': 0.0, 'positive': 1.0986122886681098}, 'Consisting': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, 'Gallup': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, 'Total': {'neutral': 0.8109302162163288, 'negative': 0.0, 'positive': 0.4054651081081644}, 'ADPnews': {'neutral': 0.0, 'negative': 0.0, 'positive': 0.0}, 'meteorological': {'neutral': 0.0, 'negative': 0.0, 'positive': 1.0986122886681098}, '710.3': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, '087': {'neutral': 1.0986122886681098, 'negative': 0.0, 'positive': 0.0}, 'glasses': {'neutral': 1.09861228866810

In [ ]:
import numpy as np
def predict(test_text,tf_icf_prob,cat_prob):
  text_feat=[txt.split() for txt in test_text] 
  catmap=['neutral','negative','positive']
  out_cat_list=list()
  for text_ft in text_feat:
    prob_vect=np.ones(3)
    for ft in text_ft:
      vals=np.ones(3).tolist()
      if ft in tf_icf_prob:
        vals= np.array(list(tf_icf_prob[ft].values()))
      prob_vect=np.multiply(prob_vect,vals)
      prob_vect=np.multiply(prob_vect,cat_prob)
    max_ind=np.argmax(prob_vect)
    cat=catmap[max_ind]
    out_cat_list.append(cat)
  return out_cat_list

In [ ]:
from sklearn.model_selection import train_test_split
train,test=train_test_split(data_df,train_size=0.7)

NameError: ignored

In [ ]:
from sklearn.metrics import accuracy_score

tf_icf_dict,tf_icf_prob=get_tf_icf_score(train)
cat_prob_dict=make_category_prob(train)
cat_pred=predict(test['text'],tf_icf_prob,list(cat_prob_dict.values()))
print(accuracy_score(cat_pred,test['sentiment']))


##Organized Final Code

In [1]:
#upload and view the dataset
from google.colab import files
uploads=files.upload()                                        # please upload the csv file

Saving BBC_News.csv to BBC_News.csv


In [3]:
import pandas as pd

df = pd.read_csv("/content/BBC_News.csv")                     # read the csv file
df                                                            # show the dataset

ArticleId                                               Text  \
0          1833  worldcom ex-boss launches defence lawyers defe...   
1           154  german business confidence slides german busin...   
2          1101  bbc poll indicates economic gloom citizens in ...   
3          1976  lifestyle  governs mobile choice  faster  bett...   
4           917  enron bosses in $168m payout eighteen former e...   
...         ...                                                ...   
1485        857  double eviction from big brother model caprice...   
1486        325  dj double act revamp chart show dj duo jk and ...   
1487       1590  weak dollar hits reuters revenues at media gro...   
1488       1587  apple ipod family expands market apple has exp...   
1489        538  santy worm makes unwelcome visit thousands of ...   

           Category  
0          business  
1          business  
2          business  
3              tech  
4          business  
...             ...  
1485  entertainment  
1486  entertainment  
1487       business  
1488           tech  
1489           tech  

[1490 rows x 3 columns]

In [16]:
list(df['Category'].unique())

['business', 'tech', 'politics', 'sport', 'entertainment']

### Data Preprocessing

In [4]:
# importing preprocessing libraries
import re
import nltk
nltk.download('stopwords')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


In [5]:
stop_words=list(stopwords.words("english"))
lemm = WordNetLemmatizer()

for i in range(len(df['Text'])):
  df['Text'][i] = df['Text'][i].lower()                           # coverting the news text to lower case
  df['Text'][i] = re.sub(("[^\w\s]"),' ',df['Text'][i])           # removing punctuations and special characters from the text
  tokens = df['Text'][i].split(" ")                               # extracting the space seperated tokens from the file to a list called 'tokens'
  new_tokens = [t for t in tokens if t not in stop_words]         # filtering the tokens which are not stop words into a new list 'new_tokens'
  word_toks = [t for t in new_tokens if t!=' ']                   # removing blank space tokens
  lemm_words = list()
  for word in word_toks:
    lemm_val=lemm.lemmatize(word,pos="v")                         # lemmatizing the words of a news text
    lemm_words.append(lemm_val)
  df['Text'][i] = lemm_words                                      # overwriting the preprocessed tokenized news text to the dataframe

df                                                                # show the dataframe

<ipython-input-5-ebdf057203d8>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Text'][i] = df['Text'][i].lower()                           # coverting the news text to lower case
<ipython-input-5-ebdf057203d8>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Text'][i] = re.sub(("[^\w\s]"),' ',df['Text'][i])           # removing punctuations and special characters from the text
<ipython-input-5-ebdf057203d8>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#re

ArticleId                                               Text  \
0          1833  [worldcom, ex, boss, launch, defence, lawyers,...   
1           154  [german, business, confidence, slide, german, ...   
2          1101  [bbc, poll, indicate, economic, gloom, citizen...   
3          1976  [lifestyle, , govern, mobile, choice, , faster...   
4           917  [enron, boss, , 168m, payout, eighteen, former...   
...         ...                                                ...   
1485        857  [double, eviction, big, brother, model, capric...   
1486        325  [dj, double, act, revamp, chart, show, dj, duo...   
1487       1590  [weak, dollar, hit, reuters, revenues, media, ...   
1488       1587  [apple, ipod, family, expand, market, apple, e...   
1489        538  [santy, worm, make, unwelcome, visit, thousand...   

           Category  
0          business  
1          business  
2          business  
3              tech  
4          business  
...             ...  
1485  entertainment  
1486  entertainment  
1487       business  
1488           tech  
1489           tech  

[1490 rows x 3 columns]

In [6]:
# importing other libraries
from os import setgroups
import math
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report

In [14]:
class classifier:

  def __init__(self,data):
    self.data_df,self.test_df = train_test_split(data,train_size=0.7)
    self.categories = list(data['Category'].unique())
    self.cat_count = len(self.categories)
    self.vocab = list()
    self.cat_dict=dict()
    self.cat_prob_dict=dict()
    self.tf_dict=dict()
    self.icf_dict=dict()
    self.tf_icf_dict=dict()
    self.tf_icf_prob=dict()

  def build_vocab(self):
    for cat in self.categories:
      self.cat_dict[cat]=list()
    for cat in self.categories:
      df_temp = self.data_df[self.data_df['Category']==cat]
      for txt in df_temp['Text']:
        self.cat_dict[cat].extend(txt)
    wd_list = set()
    for txt in self.data_df['Text']:
      wd_list = wd_list.union(set(txt))
    self.vocab=list(wd_list)

  def term_frequency_icf_find(self):
    self.build_vocab()
    for wd in self.vocab:
      self.tf_dict[wd]=dict()
      for cat in self.categories:
        self.tf_dict[wd][cat] = 0
    for cat in self.categories:
      for wd in self.cat_dict[cat]:
        self.tf_dict[wd][cat] += 1
    for wd in self.vocab:
      cnt = 0
      for cat in self.categories:
        if self.tf_dict[wd][cat]>0:
          cnt += 1
      self.icf_dict[wd] = math.log(float(self.cat_count/cnt))

  def get_tf_icf_score(self):
    self.term_frequency_icf_find()
    for wd in self.vocab:
      self.tf_icf_dict[wd]=dict()
      for cat in self.categories:
        self.tf_icf_dict[wd][cat]=self.tf_dict[wd][cat]*self.icf_dict[wd]
    for wd in self.vocab:
      self.tf_icf_prob[wd]=dict()
      for cat in self.categories:
        s = sum(self.tf_icf_dict[wd].values())
        if s > 0:
            self.tf_icf_prob[wd][cat]=self.tf_icf_dict[wd][cat] s
        else:
          self.tf_icf_prob[wd][cat] = 0.001   

  def make_category_prob(self):
    l=len(self.data_df)
    for cat in self.categories:
      data = self.data_df[self.data_df['Category']==cat]
      lp=len(data)
      self.cat_prob_dict[cat]= lp/l


  def predict(self,text_feat):
    catmap = list(self.categories)
    cat_prob = list(self.cat_prob_dict.values())
    out_cat_list=list()
    for text_ft in text_feat:
      prob_vect=np.ones(self.cat_count)
      for ft in text_ft:
        vals=np.ones(self.cat_count).tolist()
        if ft in self.tf_icf_prob:
          vals= np.array(list(self.tf_icf_prob[ft].values()))
        prob_vect=np.multiply(prob_vect,vals)
        prob_vect=np.multiply(prob_vect,cat_prob)
      max_ind=np.argmax(prob_vect)
      cat=catmap[max_ind]
      out_cat_list.append(cat)
    return out_cat_list

  def result(self):
    self.get_tf_icf_score()
    self.make_category_prob()
    cat_pred = self.predict(self.test_df['Text'])
    print("Accuracy = ",accuracy_score(self.test_df['Category'],cat_pred))
    print("Precision = ",precision_score(self.test_df['Category'], cat_pred, average='macro'))
    print("Recall = ",recall_score(self.test_df['Category'], cat_pred, average='macro'))
    print("Macro-F1 score = ",f1_score(self.test_df['Category'], cat_pred, average='macro'))
    print("\n\n\n------------------ classification Report--------------------\n")
    print(classification_report(self.test_df['Category'], cat_pred, target_names=['business', 'tech', 'politics', 'sport', 'entertainment']))

    


In [17]:
c = classifier(df)
c.result()

Accuracy =  0.2371364653243848
Precision =  0.44639639639639644
Recall =  0.20659546061415218
Macro-F1 score =  0.08829317923204322



------------------ classification Report--------------------

               precision    recall  f1-score   support

     business       0.23      1.00      0.38       103
         tech       0.00      0.00      0.00        80
     politics       1.00      0.01      0.03        70
        sport       1.00      0.02      0.04       107
entertainment       0.00      0.00      0.00        87

     accuracy                           0.24       447
    macro avg       0.45      0.21      0.09       447
 weighted avg       0.45      0.24      0.10       447



/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.9/dist-packages/sklearn/metrics/_classification.py:1344: 

In [ ]:
import math
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report
from sklearn.naive_bayes import MultinomialNB

In [ ]:
class classifier:

  def __init__(self,data):
    self.data_df,self.test_df = train_test_split(data,train_size=0.7)
    self.categories = list(data['Category'].unique())
    self.cat_count = len(self.categories)
    self.vocab = list()
    self.cat_dict=dict()
    self.cat_prob_dict=dict()
    self.tf_dict=dict()
    self.icf_dict=dict()
    self.tf_icf_dict=dict()
    self.tf_icf_prob=dict()

  def build_vocab(self):
    for cat in self.categories:
      self.cat_dict[cat]=list()
    for cat in self.categories:
      df_temp = self.data_df[self.data_df['Category']==cat]
      for txt in df_temp['Text']:
        self.cat_dict[cat].extend(txt)
    wd_list = set()
    for txt in self.data_df['Text']:
      wd_list = wd_list.union(set(txt))
    self.vocab=list(wd_list)

  def term_frequency_icf_find(self):
    self.build_vocab()
    for wd in self.vocab:
      self.tf_dict[wd]=dict()
      for cat in self.categories:
        self.tf_dict[wd][cat] = 0
    for cat in self.categories:
      for wd in self.cat_dict[cat]:
        self.tf_dict[wd][cat] += 1
    for wd in self.vocab:
      cnt = 0
      for cat in self.categories:
        if self.tf_dict[wd][cat]>0:
          cnt += 1
      self.icf_dict[wd] = math.log(float(self.cat_count/cnt))

  def get_tf_icf_score(self):
    self.term_frequency_icf_find()
    for wd in self.vocab:
      self.tf_icf_dict[wd]=dict()
      for cat in self.categories:
        self.tf_icf_dict[wd][cat]=self.tf_dict[wd][cat]*self.icf_dict[wd]
    for wd in self.vocab:
      self.tf_icf_prob[wd]=dict()
      for cat in self.categories:
        s = sum(self.tf_icf_dict[wd].values())
        if s > 0:
            self.tf_icf_prob[wd][cat]=self.tf_icf_dict[wd][cat]/s
        else:
          self.tf_icf_prob[wd][cat]=0   

  def make_category_prob(self):
    l=len(self.data_df)
    for cat in self.categories:
      data = self.data_df[self.data_df['Category']==cat]
      lp=len(data)
      self.cat_prob_dict[cat]=lp/l


  def result(self):
    self.get_tf_icf_score()
    self.make_category_prob()
    naive_bayes_classifier = MultinomialNB()
    naive_bayes_classifier.fit(self.data_df['Text'], self.data_df['Category'])
    cat_pred = naive_bayes_classifier.predict(self.test_df['Text'])
    print("Accuracy = ",accuracy_score(self.test_df['Category'],cat_pred))
    print("Precision = ",precision_score(self.test_df['Category'], cat_pred, average='macro'))
    print("Recall = ",recall_score(self.test_df['Category'], cat_pred, average='macro'))
    print("Macro-F1 score = ",f1_score(self.test_df['Category'], cat_pred, average='macro'))
    print("\n\n\n------------------ classification Report--------------------\n")
    print(classification_report(self.test_df['Category'], cat_pred, target_names=['business', 'tech', 'politics', 'sport', 'entertainment']))


## Classifier Using naive_bayes library function and standard tf-idf-vectorizer

In [48]:
# importing preprocessing libraries
import re
import nltk
nltk.download('stopwords')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
#other libraries
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report

data = pd.read_csv("/content/BBC_News.csv")   #original dataset


# preprocessing the oroginal dataframe
stop_words=list(stopwords.words("english"))
lemm = WordNetLemmatizer()
for i in range(len(data['Text'])):
  data['Text'][i] = data['Text'][i].lower()                           # coverting the news text to lower case
  data['Text'][i] = re.sub(("[^\w\s]"),' ',data['Text'][i])           # removing punctuations and special characters from the text
  tokens = data['Text'][i].split(" ")                               # extracting the space seperated tokens from the file to a list called 'tokens'
  new_tokens = [t for t in tokens if t not in stop_words]         # filtering the tokens which are not stop words into a new list 'new_tokens'
  word_toks = [t for t in new_tokens if t!=' ']                   # removing blank space tokens
  word_toks = [t for t in word_toks if t!='']
  lemm_words = list()
  for word in word_toks:
    lemm_val=lemm.lemmatize(word,pos="v")                         # lemmatizing the words of a news text
    lemm_words.append(lemm_val)
  data['Text'][i] = ' '.join(lemm_words)                                    # overwriting the preprocessed tokenized news text to the dataframe


# getting train and test data from the original dataframe
train, test = train_test_split(data,train_size=0.7)

# feature extraction
tf_vectorizer = CountVectorizer() # or term frequency
train_X = train['Text']   
train_y = train['Category']   
test_X = test['Text']
test_y = test['Category']
X_train_tf = tf_vectorizer.fit_transform(train_X)
X_test_tf = tf_vectorizer.transform(test_X)

#training model
naive_bayes_classifier = MultinomialNB()
naive_bayes_classifier.fit(X_train_tf, train_y)

# prediction and result
cat_pred = naive_bayes_classifier.predict(X_test_tf)
print("\n\n\n\nAccuracy = ",accuracy_score(test_y,cat_pred))
print("Precision = ",precision_score(test_y, cat_pred, average='macro'))
print("Recall = ",recall_score(test_y, cat_pred, average='macro'))
print("Macro-F1 score = ",f1_score(test_y, cat_pred, average='macro'))
print("\n\n\n------------------ classification Report--------------------\n")
print(classification_report(test_y, cat_pred, target_names=['business', 'tech', 'politics', 'sport', 'entertainment']))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
<ipython-input-48-20324cd87f96>:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Text'][i] = data['Text'][i].lower()                           # coverting the news text to lower case
<ipython-input-48-20324cd87f96>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Text'][i] = re.sub(("[^\w\s]"),' ',data['Text'][i])           # removing punctuations and special characters from 





Accuracy =  0.9731543624161074
Precision =  0.9693048658618872
Recall =  0.9734975997599762
Macro-F1 score =  0.9709815953912546



------------------ classification Report--------------------

               precision    recall  f1-score   support

     business       0.98      0.94      0.96       101
         tech       0.99      0.95      0.97        88
     politics       0.96      0.99      0.98        80
        sport       1.00      1.00      1.00       112
entertainment       0.92      0.98      0.95        66

     accuracy                           0.97       447
    macro avg       0.97      0.97      0.97       447
 weighted avg       0.97      0.97      0.97       447



In [46]:
# model using stemmer

# importing preprocessing libraries
import re
import nltk
nltk.download('stopwords')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.stem.snowball import SnowballStemmer
#other libraries
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report

data = pd.read_csv("/content/BBC_News.csv")   #original dataset


# preprocessing the oroginal dataframe
stop_words=list(stopwords.words("english"))
snow_stemmer = SnowballStemmer(language='english')
for i in range(len(data['Text'])):
  data['Text'][i] = data['Text'][i].lower()                           # coverting the news text to lower case
  data['Text'][i] = re.sub(("[^\w\s]"),' ',data['Text'][i])           # removing punctuations and special characters from the text
  tokens = data['Text'][i].split(" ")                               # extracting the space seperated tokens from the file to a list called 'tokens'
  new_tokens = [t for t in tokens if t not in stop_words]         # filtering the tokens which are not stop words into a new list 'new_tokens'
  word_toks = [t for t in new_tokens if t!=' ']                   # removing blank space tokens
  word_toks = [t for t in word_toks if t!='']
  stem_words = []
  for w in word_toks:
      x = snow_stemmer.stem(w)                                    # applying snowball stemmer to the list of lemmatized words
      stem_words.append(x)
  data['Text'][i] = ' '.join(stem_words)                                    # overwriting the preprocessed tokenized news text to the dataframe
 
 
# getting train and test data from the original dataframe
train, test = train_test_split(data,train_size=0.7)

# feature extraction
tf_vectorizer = CountVectorizer() # or term frequency
train_X = train['Text']   
train_y = train['Category']   
test_X = test['Text']
test_y = test['Category']
X_train_tf = tf_vectorizer.fit_transform(train_X)
X_test_tf = tf_vectorizer.transform(test_X)

#training model
naive_bayes_classifier = MultinomialNB()
naive_bayes_classifier.fit(X_train_tf, train_y)

# prediction and result
cat_pred = naive_bayes_classifier.predict(X_test_tf)
print("\n\n\n\nAccuracy = ",accuracy_score(test_y,cat_pred))
print("Precision = ",precision_score(test_y, cat_pred, average='macro'))
print("Recall = ",recall_score(test_y, cat_pred, average='macro'))
print("Macro-F1 score = ",f1_score(test_y, cat_pred, average='macro'))
print("\n\n\n------------------ classification Report--------------------\n")
print(classification_report(test_y, cat_pred, target_names=['business', 'tech', 'politics', 'sport', 'entertainment']))


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
<ipython-input-46-676b03bc7455>:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Text'][i] = data['Text'][i].lower()                           # coverting the news text to lower case
<ipython-input-46-676b03bc7455>:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Text'][i] = re.sub(("[^\w\s]"),' ',data['Text'][i])           # removing punctuations and special characters from 





Accuracy =  0.970917225950783
Precision =  0.9703575091388034
Recall =  0.9696282271944924
Macro-F1 score =  0.9698404524104388



------------------ classification Report--------------------

               precision    recall  f1-score   support

     business       0.97      0.96      0.97       112
         tech       0.97      0.96      0.97        75
     politics       0.99      0.96      0.97        75
        sport       1.00      1.00      1.00       102
entertainment       0.92      0.96      0.94        83

     accuracy                           0.97       447
    macro avg       0.97      0.97      0.97       447
 weighted avg       0.97      0.97      0.97       447

